<a href="https://colab.research.google.com/github/paulodowd/GoogleColab_Simple2DSimulator/blob/main/Sheet1_2D_Simulator.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Introduction

**Before you start**, you should have read the worksheet which describes the skills you need and how to operate these following worksheets.  [link]

In this series of exercise sheets we are going to explore using a simple 2D simulator, and then learn how we can improve it.  By following these exercises, we are going to learn about:
- Programming a controller for a simulated wheeled mobile robot.
- The challenges faced when using a real sensor:
  - Simulation & The Reality Gap.
  - Developing a simple model of a Proximity Sensor.
  - Noise & Error.
- Evaluating a more robust controller for a robot.

**To get started**, we first of all need to become familiar with the 2D simulator we are going to use. This exercise sheet has a working 2D simulator embedded within it, and you can review all the code to see how it works.  

**By the end of this worksheet**, you should have written a simple controller so that your simulated robot can drive around without crashing into obstructions.  You can work to achieve the highest score, and you can compare this with your friends progress.

**In the next worksheet**, we will begin our exercises to improve the simulator, looking specifically at a proximity sensor.  



# About the 2D Simulator

This 2D simulator simulates a robot similar to an **e-puck**:
<table><tr><td>
<p align="center">
<img src="https://static.generation-robots.com/9584-product_cover/e-puck-programmable-robot-with-battery.jpg" width="300">
</p>
</td><td>
<p align="center">
<img src="https://www.researchgate.net/profile/Kevin-Nickels-2/publication/289404595/figure/fig4/AS:499790165311491@1496170670005/Overhead-view-of-an-E-Puck-robot-with-the-angles-between-proximity-sensors-labeled-from.png" width="300">
</p>
</td></tr></table>

The robot can move around on two wheels, placed on opposite sides of the robot.  The robot has 8 infra-red proximity sensors which make observations along the red lines in the image above, used to detect obstacles in the environment.  We can program the robot to drive around, turn on the spot, and use it's sensors to avoid colliding with obstacles.  

Our simulated robot looks like the following:

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/images/WheelSpeeds.png?raw=true">
</p>

Our robot is represented as a blue dot.  A yellow line is used to indicate the forward direction of the robot.  We can control the motion of the robot by providing values between `-1.00` and `+1.00` to the left and right motors (wheels).  We can cause our robot to move forwards like so:

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/images/MovesForwards.png?raw=true">
</p>

We can cause our robot to move backwards like so:

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/images/MovesBackwards.png?raw=true">
</p>

We can cause our robot to rotate to the left or right, by writing negative and positive values to each respective motor:

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/images/Rotates.png?raw=true">
</p>

The robot has 8 sensors, like the e-puck robot.  These are marked by the red dots:

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/images/Sensors.png?raw=true">
</p>

We can see that the sensors are arranged in the same way as the e-puck. It is important to note that the two sensors facing most forwards are numbers `0` and `7` - this might not be as you expect.  All the sensors are set to have a maximum range of 20cm.  The robot body is set to 10cm diameter.  So this simulated robot can detect obstacles at a distance of two-body-lengths.  

Near the bottom of this worksheet you can see the simulator output proper.  For now, the simulation output looks like the following:

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/images/SimOutput.png?raw=true">
</p>

In the output, you can see:
- a visualisation of when the sensors are detecting objects via the `sensor beam`.  If an object is not detected, a beam is not drawn.  
- obstructions to the robot are drawn as `yellow circles`.  If your robot collides with an obstruction, it will change colour from blue to red.  
- A score: 
  - your robot will score higher if it can drive in a straight line.  
  - your robot will score badly if it collides with an obstacle or does not move.









# Preliminary Code

The following cells contain the code for the elements inside the simulator.  You can read these if you wish.  **It is requested that you do not edit any of these cells yet.**  You will come back in later worksheets to improve these.

## Obstacles

Below is a very simple model of an obstacle. We represent an obstacle as a point in 2D space, with a radius. This means it will appear as a circle. Looking at the below code, the obstacle will be located in the global coordinate space at x,y, and it will have a radius of 10 by default. Click '>' to compile before proceeding.

In [ ]:
from math import *
import numpy as np

class Obstacle_c:
  
  # Assigns itself a random position within
  # the arena, keeping a set distance from
  # the centre
  def __init__(self, arena_size=200, radius=10, rot=0.0, max_obstacles=1):
    
    self.radius = radius

    # For defined placement
    rot_ang = rot * ((np.pi*2)/max_obstacles)
    rand_dist = np.random.uniform(2.35, 2.65) * (arena_size/2)
    self.x = (arena_size/2) + rand_dist*np.cos(rot_ang)
    self.y = (arena_size/2) + rand_dist*np.sin(rot_ang)
    
    
    # For random placement
    #rand_ang = np.random.random() * (np.pi*2)
    #rand_dist = np.random.uniform(.25, .50) * (arena_size/2)
    #self.x = (arena_size/2) + rand_dist*np.cos(rand_ang)
    #self.y = (arena_size/2) + rand_dist*np.sin(rand_ang)
    

## Proximity Sensors

The below is a simple model and functions for a proximity sensor.  We will develop this sensor further in the next couple of worksheets.  Click to compile before proceeding.

In [ ]:
from math import *
import numpy as np


#
# The model of the proximity sensor.
#
#
class ProxSensor_c:
  
  # current global xy position of sensor
  x = 0
  y = 0
  theta = 0
  
  # To store the last sensor reading
  reading = 0

  # To set sensor local position around the robot body.
  offset_dist = 0
  offset_angl = 0

  # maximum scan range:
  max_range = 20

  # constructor. by default, sensor sits 10 distance forward
  # and faces 0 radians with respect to robot origin (0,0).
  def __init__(self, offset_dist=5, offset_angl=0):
    self.offset_dist = offset_dist
    self.offset_angl = offset_angl


  def updateGlobalPosition(self, robot_x, robot_y, robot_theta ):

    # Current direction of the sensor is the rotation
    # of the robot body plus the fixed rotation of the 
    # sensor around that same body.
    self.theta = self.offset_angl + robot_theta

    # With the rotation, we now work out where the 
    # sensor sits in cartesian space (x,y) by projecting
    # out by offset_distance.
    # Note, we do this as if the sensor was at origin (0,0)
    sensor_x = (self.offset_dist*np.cos(self.theta))
    sensor_y = (self.offset_dist*np.sin(self.theta))

    # commit new position to memory, translating to the 
    # robots current x,y position.
    self.x = sensor_x + robot_x
    self.y = sensor_y + robot_y

    # If we've reset position, the last sensor reading
    # is now wrong.  
    self.reading = -1

  def scanFor( self, obstruction ):

    # See if the obstruction is within the detection
    # range of the sensor.
    distance = np.sqrt( ((obstruction.x - self.x)**2) + ((obstruction.y - self.y)**2) )
    distance = distance - obstruction.radius

    # if out of range, return error
    # note: real sensors aren't this easy.
    if distance > self.max_range:
      return

    # compute this sensors angle toward the obstruction
    # (e.g. where is the object relative to the sensor?)
    a2o = atan2( ( obstruction.y - self.y), (obstruction.x-self.x ))

    # computer the smallest angle between the line of 
    # sight of the sensor, and the current angle to the
    # obstruction.
    # [insert url here]
    angle_between = atan2( sin(self.theta-a2o),  cos(self.theta-a2o) )
    angle_between = abs( angle_between )
    
    # If the detection is outside of the field of view
    # of the sensor, then we return and do nothing else.
    # This will either leave the reading as -1 (invalid)
    # for the next call.  Or leave the reading as the
    # last valid reading (>-1) it had.
    if angle_between > np.pi/8:
      return

    # If the current reading is -1 then that means
    # this is the first valid reading, and we update
    # the sensor.
    if self.reading < 0:
      self.reading = distance

    # If the sensor already has a valid reading (>-1)
    # then we only store the new reading if it is closer.
    # (closer obstructions block the field of view)
    if self.reading > 0:
      if distance < self.reading:
        self.reading = distance





## The Robot

The below is a simple model of a robot, which includes the proximity sensor above.  Click to compile before proceeding.

In [ ]:

from math import *
import numpy as np

#
# The model of the robot.
#
#
class Robot_c:
  
  # We could do something like, manually add 2 sensors  
  #prox_sensors.append( ProxSensor_c(2, np.pi/8) )
  #prox_sensors.append( ProxSensor_c(2, -np.pi/8) )

  def __init__(self, x=50,y=50,theta=np.pi):
    self.x = x
    self.y = y
    self.theta = np.pi# theta
    self.stall = -1 # to check for collisions
    self.score = 0
    self.radius = 5 # 5cm radius
    self.wheel_sep = self.radius*2 # wheel on either side
    self.vl = 0
    self.vr = 0
    
    # This is the body plan of sensors from
    # an e-puck robot! (in radians)
    self.sensor_dirs = [0.296706,
                        0.8726646, 
                        1.570796,
                        2.617994, 
                        3.665191, 
                        4.712389,
                        5.410521, 
                        5.986479]

    self.prox_sensors = [] #= ProxSensor_c()
    for i in range(0,8):
      self.prox_sensors.append( ProxSensor_c(self.radius, self.sensor_dirs[i]) )


  def updatePosition( self, vl, vr ):

    if vl > 1.0: 
      vl = 1.0
    if vl < -1.0:
      vl = -1.0
    if vr > 1.0:
      vr = 1.0
    if vr < -1.0:
      vr = -1.0

    # save requested wheel speed for later.
    self.vl = vl
    self.vr = vr

    # clear stall flag, attempt move
    self.stall = -1

    # robot matrix, contributions to motion x,y,theta
    r_matrix = [(vl/2)+(vr/2),0, (vr-vl)/self.wheel_sep]

    # kinematic matrix  
    k_matrix = [
                [ np.cos(self.theta),-np.sin(self.theta),0],
                [ np.sin(self.theta), np.cos(self.theta),0],
                [0,0,1] 
               ]

    result_matrix = np.matmul( k_matrix, r_matrix)

    self.x += result_matrix[0]
    self.y += result_matrix[1]
    self.theta -= result_matrix[2]

    # Once we have updated the robots new global position
    # we should also update the position of its sensor(s)
    for prox_sensor in self.prox_sensors:
      prox_sensor.updateGlobalPosition( self.x, self.y, self.theta )



  # The sensor checks if it is in range to an obstruction,
  # and if yes, calculates the simulated proximity reading.
  # if no, determines and error result.
  def updateSensors(self, obstruction ):

    # for each sensor
    # for each obstruction
    for prox_sensor in self.prox_sensors:
      prox_sensor.scanFor( obstruction ) 

  def collisionCheck(self, obstruction ):
    distance = np.sqrt( ((obstruction.x - self.x)**2) + ((obstruction.y - self.y)**2) )
    distance -= self.radius
    distance -= obstruction.radius
    if distance < 0:
      self.stall = 1
      angle = atan2( obstruction.y - self.y, obstruction.x - self.x)
      self.x += distance * np.cos(angle)
      self.y += distance * np.sin(angle)
    
  def updateScore(self):
    
    # 1 minus the difference between wheel speed
    # to encourage straight line travel.  
    # square root rewards small differences
    diff = np.abs(((self.vl+1) - (self.vr + 1))) * 0.5
    
    if diff > 0.0:
      diff =  1 - np.sqrt( diff )
    else:
      diff = 1 # - 0
    
    
    # Reward motor activation / penalise no movement
    vel = (np.abs(self.vl) + np.abs(self.vr))/2
    
    

    new_score = vel * diff

    

    if self.stall == 1:
      new_score -= 3   

    self.score += new_score
      

# Exercise 1: Create your own Robot Controller


The below two cells contain the code for the **controller** and the **simulator**.  It might be useful to first go and run the controller and then run the simulator to see what the output looks like. 

Once you have done this, you can edit the below controller to change the behavior of the robot.  You are welcome to ask for support if something is confusing or you do not understand.

You should:
- run the controller cell, and then the simulator cell, and view the output.
- begin to edit the controller to create your own obstacle avoidance behaviour:

  - how should the robot turn behaviour be effected with respect to the distance of a detected obstacle?
  - which sensors are useful?
  - do you need to use all sensors?
  - is there a useful way to process the sensor distance measurement?
  - 

## The Controller

The below function is the "controller" called by the robot.  The **controller** is the part of the robot software which must decide how the robot should act.  

A robot needs **you** to first of all understand the task, and then write some rules, logic, or intelligence in code so the robot will make autonomous decisions.  This is actually very difficult, because we have to imagine all the different circumstances a robot may encounter. 

In this controller, we need to read the proximity sensors, make a decision, and then set the motor power.  The below class is a minimal template.  You can edit this controller to produce more interesting and intelligent behaviour from your robot.  

In [ ]:
# Not done yet.

class Controller_c:

  def __init__ (self):
    self.test = 1

  def update( self, robot ):
    vl = 0.4# + np.random.normal(0,0.2)
    vr = 0.4# + np.random.normal(0,0.2)

    thrust = 0

    # for brevity
    s = robot.prox_sensors
    if s[0].reading > 0:
      thrust += (( s[0].max_range - s[0].reading ) / s[0].max_range)  * -1.1
    if s[1].reading > 0:
        thrust += (( s[1].max_range - s[1].reading ) / s[1].max_range) * -1.15
    if s[2].reading > 0:
        thrust += (( s[2].max_range - s[2].reading ) / s[2].max_range) * -1.2
    
    if s[7].reading > 0:
        thrust += (( s[7].max_range - s[7].reading ) / s[7].max_range) * 1.15
    if s[6].reading > 0:
        thrust += (( s[6].max_range - s[6].reading ) / s[6].max_range) * 1.2
    if s[5].reading > 0:
        thrust += (( s[5].max_range - s[5].reading ) / s[5].max_range) * 1.3
    
    vl += thrust
    vr -= thrust
    
    return vl, vr



## The 2D Simulator

The below code is the Simulator itself, which produces an interactive graph as an output.  Note that, when you run this code pane, it will take some time to execute and to produce the result.  The results is displayed at the bottom as an interactive plot.

In [ ]:

import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation

%matplotlib inline

# To produce our animated simulation output
from matplotlib import rc
rc('animation', html='jshtml')

# Constants which define the simulator
# We do not need to change these.
numframes = 150
arena_width = 200
num_obstacles = 12


#------------------------------------------------------------
# set up figure and animation
fig = plt.figure(dpi=120)
#fig.subplots_adjust(left=0, right=1, bottom=0, top=1)
ax = fig.add_subplot(111, aspect='equal', autoscale_on=False,
                     xlim=(0, arena_width), ylim=(0, arena_width))


# An instance of our simulated Robot!
# Placed in the centre of the arena.
my_robot = Robot_c(arena_width/2,arena_width/2,np.random.random()*np.pi*2)

gui_robot, = ax.plot([], [], 'bo', ms=my_robot.radius*2)
gui_robot.set_data([], [])
gui_dir, = ax.plot([], [], 'r-', c="yellow")
gui_sensor = ax.plot( *[[],[]]*num_obstacles,'r-', c="red")

gui_obstacles, = ax.plot([],[],'bo', ms=24, c="orange")
# A list of obstacles within the space
obstacles = []
obstacles_xy = []
for i in range( num_obstacles ):
  obstacles.append( Obstacle_c( arena_width, 12, i, num_obstacles) )
  obstacles_xy.append( [obstacles[i].x, obstacles[i].y] )

obstacles_xy = np.asarray( obstacles_xy, dtype=float)
gui_obstacles.set_data( obstacles_xy[:,0], obstacles_xy[:,1]  )

# An instance of our controller!
my_controller = Controller_c()


def animate(i):
    
    global ax, fig
    

    # Use controller to set new motor speeds in
    # range [-1.0:+1.0]
    # Note, uses sensor information from prior
    # simulation cycle.
    vl, vr = my_controller.update( my_robot )
    
    # Update robot position, check for collision,
    # then update sensors.
    my_robot.updatePosition(vl, vr)
    for obstacle in obstacles:
      my_robot.collisionCheck( obstacle )
      my_robot.updateSensors( obstacle )

    # Draw the robot, change colour for collision
    gui_robot.set_data(my_robot.x, my_robot.y)
    if my_robot.stall == 1:
      gui_robot.set_color("red")
    else:
      gui_robot.set_color("blue")
    
    # Draw a little indicator so we can see which
    # way the robot is facing
    tx = my_robot.x + (my_robot.radius*1.4*np.cos(my_robot.theta))
    ty = my_robot.y + (my_robot.radius*1.4*np.sin(my_robot.theta))
    gui_dir.set_data( (my_robot.x,tx), (my_robot.y, ty) )


    # Draw the sensor beams
    for i in range(8):
      prox_sensor = my_robot.prox_sensors[i]
      ox = prox_sensor.x
      oy = prox_sensor.y
      if prox_sensor.reading > 0:
        tx = prox_sensor.x + prox_sensor.reading * np.cos( prox_sensor.theta)
        ty = prox_sensor.y + prox_sensor.reading * np.sin( prox_sensor.theta)
      else:
        tx = prox_sensor.x + np.cos( prox_sensor.theta)
        ty = prox_sensor.y + np.sin( prox_sensor.theta)

      gui_sensor[i].set_data( (ox,tx), (oy, ty) )
    
    # Update the current score in the title!
    my_robot.updateScore()
    ax.set_title('Score: {0:f}'.format( my_robot.score ))
    
    return gui_robot, 

plt.close()
ani = animation.FuncAnimation(fig, animate, frames=numframes, interval=10, blit=True)
ani


#plt.show()

# Exercise 2

By now you should have a controller for your robot which allows it to successfully navigate without colliding with obstacles.  It can be tricky to get good performance!

- How does your score compare to your peers?
- What techniques have your peers used, compared to you?
- With your current controller, create a list of the different scores your robot acheives.
  - How reliable would you say your controller is?